In [ ]:
!pip install pandas lxml tqdm datasets huggingface_hub

import xml.etree.ElementTree as ET
import pandas as pd
import unicodedata

import re

from huggingface_hub import login
from datasets import load_dataset, Dataset

login(token="X")

In [9]:
def normalize_arabic(text):
    if text:
        return unicodedata.normalize("NFKC", text)  # Normalize Unicode form
    return ""

# Define your XML file path
xml_file = "LMF-Cont.xml"

# Initialize list to store data
data = []

# Parse XML efficiently
context = ET.iterparse(xml_file, events=("start", "end"))
_, root = next(context)  # Get root element

In [10]:
for event, elem in context:
    if event == "end" and elem.tag == "Sense":  
        sense_id = elem.attrib.get("id", "")  # Get Sense ID

        # Extract and normalize definition
        definition_elem = elem.find("Definition/feat[@att='text']")
        definition = normalize_arabic(definition_elem.attrib.get("val", "")) if definition_elem is not None else ""

        # Extract example sentences (if multiple exist)
        examples = [normalize_arabic(ex.attrib.get("val", "")) for ex in elem.findall("SenseExample/feat[@att='text']")]

        # Append extracted data
        data.append({
            "Sense_ID": sense_id,
            "Definition": definition,
            "Examples": " | ".join(examples)  # Join multiple examples
        })

        # Clear processed elements to save memory
        elem.clear()

In [11]:
df = pd.DataFrame(data)

# Save to CSV
csv_file = "arabic_reverse_dictionary_cleaned.csv"
df.to_csv(csv_file, index=False, encoding="utf-8")

print(f"Saved {len(df)} entries to {csv_file}")

Saved 113069 entries to arabic_reverse_dictionary_cleaned.csv


In [14]:
df.head(50)

Sense_ID                                         Definition  \
0          أ2D1                                                      
1          أ2D2      حرف نداء للقريب حقيقة، أو القريب في الذِّهن .   
2          أ2D3  حرف استفهام يُستفهم به عن وقوع الشيء أو عدم وق...   
3          أ2D4  حرف استفهام يُراد به تعيين القائم بالفعل، ويجا...   
4          أ2D5     حرف استفهام للتسوية، يأتي بعد سواء أو سيَّان .   
5          أ2D6  حرف يكون في أوّل الفعل المضارع للدلالة على الم...   
6          أ2D7                                 أحد أحرف الزيادة .   
7          أ2D8  حرف يزاد في أوّل الفعل الثلاثيّ المجرّد الماضي...   
8          أ2D9   حرف استفهام خرج عن معناه الحقيقيّ يفيد التعجّب .   
9         أ2D10   حرف استفهام خرج عن معناه الحقيقيّ يفيد التهكّم .   
10        أ2D11  حرف استفهام خرج عن معناه الحقيقيّ يفيد الاستبط...   
11        أ2D12   حرف استفهام خرج عن معناه الحقيقيّ يفيد التوبيخ .   
12        أ2D13  حرف استفهام خرج عن معناه الحقيقيّ يفيد التقرير...   
13        أ2D14  حرف استفهام خرج عن معناه الحقيقيّ يفيد الإنكار...   
14        أ2D15  حرف استفهام يُعَدُّ شرطا في اكتفاء المشتقّ بمر...   
15          آD1  حرف نداء للبعيد أو ما هو في حُكْمه كالنائم وال...   
16         آبD1  الشّهر الثّامن من شهور السَّنة الشَّمسيَّة، يأ...   
17         آبD2  الأُقْنُوم أو الأصل الأوَّل من الثَّالوث الأقد...   
18      آبنوسD1   (نت) أبنوس،شجر مثمر من الفصيلة الآبنوسيّة، أو...   
19    آبنوسيةD1                                                      
20  آبنوسيَّةD2  اسم مؤنَّث منسوب إلى آبَنُوسُ/ آبُنُوسُ/ آبِنُ...   
21  آبنوسيَّةD3  مادّة صُلبة سوداء، غير موصِّلة للكهرباء، تنتج ...   
22        آجرD1  المفرد آجُرَّة: لَبِن محروق مُعدٌّ للبناء، وتت...   
23         آحD1           بياض البيض الذي يؤكل، والماحُ صُفْرتُه .   
24         آحD2  مادّة نشويّة أو بروتينيّة أو دُهنيّة في البذرة...   
25        آدمD1  أبو البشر، خلقه الله من طين وأمر الملائكة أن ت...   
26      آدَمُD2  بروز غضروفيّ ناتئ أعلى الرقبة، يتحرَّك أثناء ا...   
27       آذارD1  الشّهر الثّالث من شهور السّنة الشّمسيَّة، يأتي...   
28    آراميونD1                                      المفرد آراميّ   
29  آرامِيّونD2  شعب ساميّ عاش بين القرنين الثَّامن عشر والثَّا...   
30        آريD1                                                      
31       آريّD2  جنس تجمعه بعض الخصائص اللُّغويَّة والجنسيَّة، ...   
32       آريّD3                        من ينتمي إلى الجنس الآريّ .   
33       آريةD1                                                      
34      آريّةD2          لغة يُقال إنّها أصل اللغات الهندوأوربيّة.   
35      آريّةD3  فكرة تقول بتفوّق الجنس الآريّ، وقد استندت إليه...   
36        آزرD1  اسم أبي إبراهيم، أو لقب له، أو اسم عمّه، وكان ...   
37       آزوتD1  (كم) غاز شفّاف لا لون له ولا رائحة ولا طعم يُع...   
38      آزوتيD1  اسم منسوب إلى آزوتّ: محتوٍ على الآزوتّ (انظر: ...   
39    آزوتّيّD2  سائل لا لون له، يُطلق أبخرة خانقة في الهواء، ي...   
40        آس1D1   المفرد آسَة: (نت) شجر دائم الخضرة، بيضيّالورق...   
41        آس2D1       ورقة من أوراق اللعب ذات نقطة أو علامة واحدة.   
42       آسياD1  أَسْيا، أكبر القارات وأكثرها سكَّانًا، إذ تبلغ...   
43      آسيويD1                        اسم منسوب إلى آسْيا/ آسِيا.   
44       آمينD1  اسم فعل أمر، ومعناه: اللّهمَّ استجبْ، أو ليكن ...   
45      آنسونD1  (نت) أنيسون، يانسون؛ نبات حوليّ من فصيلة الخيم...   
46        آنكD1  رصاص أسود، أو أبيض "مَنْ جَلَس إِلى قَيْنَةٍ ل...   
47         آهD1                    (انظر: أ و هـ - آهْ/ آهِ/ آهٍ).   
48         آيD1                                                      
49        آيْD2                                  حرف نداء للبعيد .   

                                             Examples  
0                                                      
1   أبُنَيَّ لا تخشَ كلمة الحقّ | أَمَنْ هُوَ قَان...  
2   أسافر أخوك؟ نعم سافر أخي | أسافر أخوك؟ لا لم ي...  
3   أمحمَّد حاضر أم عليّ؟ مُحمَّد | وَإِنْ أَدْرِي...  
4   سواءٌ عليَّ أسافرت أم لم تسافر | إِنَّ الَّذِي...  
5                                               أقرأُ  
6                                           

In [15]:
def clean_sense_id(sense_id):
    return re.sub(r"[^ء-يًٌٍَُِّْ]", "", sense_id)  # Keeps Arabic letters and diacritics

# Apply the function to clean the column
df["Sense_ID"] = df["Sense_ID"].apply(clean_sense_id)

# Save the cleaned data
df.to_csv("arabic_reverse_dictionary_cleaned.csv", index=False, encoding="utf-8")

print("Sense_ID column cleaned successfully, diacritics preserved!")

Sense_ID column cleaned successfully, diacritics preserved!


In [19]:
df.iloc[1]

Sense_ID                                                      أ
Definition        حرف نداء للقريب حقيقة، أو القريب في الذِّهن .
Examples      أبُنَيَّ لا تخشَ كلمة الحقّ | أَمَنْ هُوَ قَان...
Name: 1, dtype: object

In [22]:
# Find rows where Sense_ID or Definition is empty or NaN
empty_rows = df[(df["Definition"].isna()) | (df["Definition"] == "")]

# Print the number of empty rows found
print(f"Number of empty rows: {len(empty_rows)}/ {len(df)}")

# Display the first few empty rows (if any)
print(empty_rows.head())

Number of empty rows: 0/ 113069
Empty DataFrame
Columns: [Sense_ID, Definition, Examples]
Index: []


In [ ]:
# remove rows with no definition
df = df[~(df["Definition"].isna() | (df["Definition"] == ""))]

print(len(df))

# check again
empty_rows = df[(df["Definition"].isna()) | (df["Definition"] == "")]
print(f"Number of empty rows: {len(empty_rows)}/ {len(df)}")

106432
Number of empty rows: 0/ 106432


In [ ]:
# rename the Sense_ID column to Terminology
df.rename(columns={"Sense_ID": "Terminology"}, inplace=True)

In [25]:
# upload to hugging face
dataset = Dataset.from_pandas(df)

dataset.push_to_hub("FlouBsy/Arabic-Terminologies-and-Definitions")


[notice] A new release of pip is available: 24.3.1 -> 25.0
[notice] To update, run: pip install --upgrade pip
The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: fineGrained).
Your token has been saved to /home/floubsy2423/.cache/huggingface/token
Login successful


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/107 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/FlouBsy/Arabic-Terminologies-and-Definitions/commit/0b0c924884f0beb8f7ad2c76ae699cc8cffd54ff', commit_message='Upload dataset', commit_description='', oid='0b0c924884f0beb8f7ad2c76ae699cc8cffd54ff', pr_url=None, pr_revision=None, pr_num=None)